# 群体药动学建模


在本节中，我们将学习如何利用 Masmod 构建简单的群体药动学模型，并学习使用 Notebook 工具。

在开始前，推荐先阅读：{doc}`Python 编程语言入门 <../pre/python-basics>`、{doc}`Python 数据科学入门 <../pre/python-data-science>`、{doc}`Markdown 语法 <../pre/markdown-syntax>`。


## 定量药理学和群体药动学

定量药理学（pharmacometrics）是一门结合传统药理学理论与数学模型而形成的新兴学科，其主要通过建模与模拟的方法来定量描述、阐释和预测药物在人体内的吸收、分布、代谢和排泄的特征、药物在人体内的药效特征及其两者的相关性。

群体药动学（population pharmacokinetics）是定量药理学的重要研究方向之一，与传统的标准两步法（standard two stage）相比，群体药动学利用构建模型的方法来有效整合多个临床研究的数据，在获取药物药动学参数群体典型值及其影响因素的同时，也能通过模型定量诠释药物在体内的药动学特征并进行模拟预测，能大大缩短临床研究所需的人力与时间成本，是模型引导的药物开发（model-informed drug development，MIDD）流程中的应用最广泛也是最关键的技术之一。

:::{note}
若你想了解更多有关于群体药动学的知识，可参考：

- [国家药监局药审中心. (2020). 群体药代动力学研究技术指导原则.](https://www.cde.org.cn/main/news/viewInfoCommon/b3e8205a4749caa0264414514cdf45ac)。

若你想了解有关于 MIDD 的内容，可参考：

- [国家药监局药审中心. (2020). 模型引导的药物研发技术指导原则.](https://www.cde.org.cn/main/news/viewInfoCommon/23b634adf79ecd4616bb91bcd66815f0)。

若你想深入学习群体药动学建模模拟方法，可参考：

- _焦正. (2019). 基础群体药动学和药效学分析. 科学出版社_。

:::


## Notebook 的创建和使用

我们的 Notebook 参考开源项目 [Jupyter Notebook](https://jupyter.org/) 开发。Jupyter Notebook 相关插件在 VSCode 中的下载量已达上亿数量级，是时下最为流行和便利的数据科学工具之一。

我们软件中的 Notebook 同样提供了这样一个交互式计算平台，允许创建一个包含文本、图形、代码的可交互式文档，为你带来全新的数据分析和建模模拟体验。

下文中我们将先简单学习如何使用软件中的 Notebook。


1. 和新建分析一致，我们可以在新建分析页内选择 **“通用 > Notebook”** 来创建一个新的 Notebook（{numref}`tutorial-new-notebook`）。

```{figure} ../../_static/tutorial-new-notebook.png
:align: center
:name: tutorial-new-notebook

“Notebook” 选项示意图
```

2. 在新建的 Notebook 中，我们便可以开始尝试在单元格中输入 Python 代码了。我们试着输入如下代码，并点击左侧的 ![单元格运行按钮](../../_static/button-run-cell.png) 按钮以运行代码。运行后，你应该可以看到在单元格下打印出了 “Hello, World!”（{numref}`tutorial-poppk-notebook-start`）。


In [1]:
print("Hello, World!")

Hello, World!


```{figure} ../../_static/tutorial-poppk-notebook-start.png
:align: center
:name: tutorial-poppk-notebook-start

Hello, World! 代码执行后示意图
```


3. 我们可以点击标签页顶部工具栏中的 **“+ 代码”** 按钮来新增一个代码单元格。也可以鼠标悬浮至此单元格下方，点击 **“+ 代码”** 按钮来新增（{numref}`tutorial-poppk-notebook-new-cell`）。在不处于单元格编辑状态时，也可以按下键盘 <kbd>B</kbd> 键来在下方新增一个单元格。接下来你可以在新增的单元格中输入代码并运行，也可以重复几次新增单元格的操作，来熟悉这一流程。


```{figure} ../../_static/tutorial-poppk-notebook-new-cell.png
:align: center
:name: tutorial-poppk-notebook-new-cell

新增代码按钮位置示意图
```


:::{Tip}
一些在 Notebook 中常用的键盘快捷键：

- <kbd>A</kbd> 在 **上方** 新增一个同类型的单元格（不处于编辑状态时）
- <kbd>B</kbd> 在 **下方** 新增一个同类型的单元格（不处于编辑状态时）
- <kbd>Ctrl</kbd> + <kbd>Enter</kbd> 运行代码或完成 Markdown 编辑
  :::


## Masmod 入门

Masmod 是一个基于 Python 编程语言的建模模拟框架，兼容 Python 数据科学生态，力图以最便捷与清晰的方式完成群体建模与模拟的工作流程。

接下来，我们将使用 Masmod 内置的血管内给药一室模型来完成对华法林示例数据集中的血药浓度数据完成群体药动学建模并采用 FOCEi（First Order Conditional Estimation with interaction）算法完成模型拟合。


1. 首先我们需要导入 Masmod 与华法林示例数据，代码如下：


In [1]:
import polars as pl


from mas.model import *
from mas.datasets import warfarin

2. 接下来我们定义一个血管内给药一室模型 `Warfarin`，同时定义模型中的群体药动学参数（例如清除率和表观分布容积）及其个体间变异：


In [2]:
class WarfarinPk(EvOneCmtLinear):
    def __init__(self) -> None:
        """ "定义模型参数"""
        super().__init__()
        self.tv_cl = theta(0.134, bounds=(0, None))
        self.tv_v = theta(7.81, bounds=(0, None))
        self.tv_ka = theta(0.571, bounds=(0, None))
        self.tv_alag = theta(0.823, bounds=(0, None))

        self.eta_cl = omega(0.049)
        self.eta_v = omega(0.0802)
        self.eta_ka = omega(0.047)
        self.eta_alag = omega(0.156)

        self.eps_prop = sigma(0.0104)
        self.eps_add = sigma(0.554)

    def pred(self) -> Expression:
        """ "定义模型结构"""
        cl = self.tv_cl * exp(self.eta_cl)
        v = self.tv_v * exp(self.eta_v)
        ka = self.tv_ka * exp(self.eta_ka)
        alag = self.tv_alag * exp(self.eta_alag)

        pred_res = self.pred_physio(cl=cl, v=v, ka=ka, alag1=alag, s2=v)
        ipred = pred_res.F

        y = ipred * (1 + self.eps_prop) + self.eps_add

        return y

3. 接着我们筛选出示例数据中的血药浓度数据（即 DVID 不等于 2 的数据）


In [3]:
pk_data = warfarin.filter(pl.col("DVID") != 2)

pk_data.head(10)

shape: (10, 11)
┌─────┬──────┬───────┬──────┬───┬─────┬─────┬───────┬──────┐
│ ID  ┆ TIME ┆ AMT   ┆ DV   ┆ … ┆ AGE ┆ SEX ┆ DOSE  ┆ EVID │
│ --- ┆ ---  ┆ ---   ┆ ---  ┆   ┆ --- ┆ --- ┆ ---   ┆ ---  │
│ i64 ┆ f64  ┆ f64   ┆ f64  ┆   ┆ i64 ┆ i64 ┆ f64   ┆ i64  │
╞═════╪══════╪═══════╪══════╪═══╪═════╪═════╪═══════╪══════╡
│ 0   ┆ 0.0  ┆ 100.0 ┆ null ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 1    │
│ 0   ┆ 0.5  ┆ null  ┆ 0.0  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 1.0  ┆ null  ┆ 1.9  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 2.0  ┆ null  ┆ 3.3  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 3.0  ┆ null  ┆ 6.6  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 6.0  ┆ null  ┆ 9.1  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 9.0  ┆ null  ┆ 10.8 ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 12.0 ┆ null  ┆ 8.6  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 24.0 ┆ null  ┆ 5.6  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
│ 0   ┆ 36.0 ┆ null  ┆ 4.0  ┆ … ┆ 50  ┆ 1   ┆ 100.0 ┆ 0    │
└─────┴──────┴───────┴──────┴───┴─────┴─────┴───────┴──────┘

4. 数据筛选完成后，我们就可以将模型与数据结合起来组成群体模型了：


In [4]:
pop_model = PopModel(mod=WarfarinPk, data=pk_data)

5. 群体模型定义完成后，我们采用 FOCEi 算法拟合模型：


In [5]:
fit_res = pop_model.fit(FOCEi(print=10))

🔧 CXX compiler C:\MaSTools\mingw64\bin\g++.EXE
📦 Compiling build target...
🔗 Linking dynamic library...
✅ Compilation Finished
✈️ First Order Conditional Estimation
Using BFGS...
* maxiter = 9999
* xtol = 1e-06
* ftol = 1e-06
* lower_bounds = 
* upper_bounds = 
* log_level = 0
* print = 10
* print_type = 0
* verbose = 1
* p_small = 0.1
* rel_step_size = 0.001

#0    ofv: 347.7917575
x: 1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  1.0000e-01  
Gradients: -1.0509e+01 -8.3374e+00 -9.6925e+01  3.0800e+01 -2.7513e+01  1.7544e+01 -3.3121e+01 -1.1511e+01  4.3184e+01  1.2218e+02
Funcalls: 8
#1    ofv: 252.9367078
x: 1.5161e-01  1.4094e-01  5.7596e-01  -5.1245e-02 2.3511e-01  1.3849e-02  2.6265e-01  1.5653e-01  -1.1206e-01 -5.0000e-01 
Gradients:  5.8501e+01  1.9482e+01 -1.2655e+01  4.3841e-01 -2.0968e+01  1.4030e+01 -3.3114e+01 -4.1979e+00  7.4639e+00  4.2037e+01
Funcalls: 17
#11   ofv: 219.1455283
x: 6.6128e-02  1.1409e-01  1.1174

6. 最后，我们来查看模型拟合结果：


In [6]:
fit_res

Estimation Summary                                                              

────────────────────────────────────────────────────────────────────────────────
    OFV       Converged      Total     Compilation   Estimation   Covariance 
                           Iterations      Time         Time         Time    
────────────────────────────────────────────────────────────────────────────────
     217.997       True ✅           24    0:00:14.9   0:00:01.45   0:00:02.21
────────────────────────────────────────────────────────────────────────────────


Parameter Estimation                                                            

────────────────────────────────────────────────────────────────────────────────
 Parameter     Estimate   Shrinkage(%)    RSE(%)   
────────────────────────────────────────────────────────────────────────────────
Theta                                              
       tv_cl        0.132                    19.193
        tv_v        7.978                     0.266
       tv_ka        1.354                    66.040
     tv_alag        0.824                    11.508
Omega(SD)                                          
      eta_cl        0.289        0.000       24.158
       eta_v        0.220        3.993        8.069
      eta_ka        0.835       50.453      284.405
    eta_alag        0.394       59.245       28.037
Sigma(SD)                                          
    eps_prop        0.086       14.952       10.149
     eps_add        0.259       15.635        2.846
────────────────────────────────────────────────────────────────────────────────